In [209]:
# import libraries
import pandas as pd
import scipy.stats as sts
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objs as go
import geopandas as gpd
# import osmnx as ox
import json
from datetime import datetime, timedelta, date
import os
import time
import pyarrow
import sys
import requests
# import sidetable
import warnings
warnings.filterwarnings('ignore')

In [210]:
sys.tracebacklimit = 0 # turn off long tracebacks on error messages
#sys.tracebacklimit = None # use to turn tracebacks back on if needed

In [211]:
pd.set_option('display.max_columns', None)
pd.set_option("display.max_rows", None)

In [213]:
# Enter latest version uuid of API (Updated weekly on Thurs. See https://data.cms.gov/covid-19/covid-19-nursing-home-data/api-docs)
latest_uuid = 'a3371812-a39f-4804-8105-7fc4bc19d57f'


In [214]:
nh_latest = []

#Data is aggregated to week. Week is Monday - Sunday,

#Enter the Sunday (week ending date) of the week you want to start on.
week_ending_start = date(2022,11,27)

#Enter the Sunday (week ending date) of the week you want to end on.
week_ending_end = date(2022,11,27)
week = timedelta(days=7)
offset = 0
size = 5000

while week_ending_start <= week_ending_end:
    
    for offset in range(0,20000,5000):
        print("---")
        url = f"https://data.cms.gov/data-api/v1/dataset/{latest_uuid}/data?filter[week_ending]={week_ending_start}&offset={offset}&size={size}"
        print("Requesting",url)
        
        response = requests.get(url)
        data = response.json()
        if len(data) == 0:
            break
        nh_latest.extend(data)
    
        offset = offset + size
        time.sleep(5)

    #when viewing output, ensure that offset increments by the size amount for each week
    print("---")
    url = f"https://data.cms.gov/data-api/v1/dataset/{latest_uuid}/data?filter[week_ending]={week_ending_start}&offset={offset}&size={size}"
    print("Requesting",url)
    
    
    week_ending_start = week_ending_start + week
    time.sleep(5)

---
Requesting https://data.cms.gov/data-api/v1/dataset/e5bf0ec8-9e47-4175-8b83-cfe526b9c0bb/data?filter[week_ending]=2022-11-27&offset=0&size=5000
---
Requesting https://data.cms.gov/data-api/v1/dataset/e5bf0ec8-9e47-4175-8b83-cfe526b9c0bb/data?filter[week_ending]=2022-11-27&offset=5000&size=5000
---
Requesting https://data.cms.gov/data-api/v1/dataset/e5bf0ec8-9e47-4175-8b83-cfe526b9c0bb/data?filter[week_ending]=2022-11-27&offset=10000&size=5000
---
Requesting https://data.cms.gov/data-api/v1/dataset/e5bf0ec8-9e47-4175-8b83-cfe526b9c0bb/data?filter[week_ending]=2022-11-27&offset=15000&size=5000
---
Requesting https://data.cms.gov/data-api/v1/dataset/e5bf0ec8-9e47-4175-8b83-cfe526b9c0bb/data?filter[week_ending]=2022-11-27&offset=20000&size=5000


In [215]:
nh_latest = pd.DataFrame(nh_latest)
nh_latest.head()


week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   

                                 provider_name             provider_address  \
0                     BURNS NURSING HOME, INC.         701 MONROE STREET NW   
1               COOSA VALLEY HEALTHCARE CENTER       260 WEST WALNUT STREET   
2                   HIGHLANDS HEALTH AND REHAB          380 WOODS COVE ROAD   
3  EASTVIEW REHABILITATION & HEALTHCARE CENTER     7755 FOURTH AVENUE SOUTH   
4                PLANTATION MANOR NURSING HOME  6450 OLD TUSCALOOSA HIGHWAY   

  provider_city provider_state provider_zip_code provider_phone_number  \
0  RUSSELLVILLE             AL             35653            2563324110   
1     SYLACAUGA             AL             35150            2562495604   
2    SCOTTSBORO             AL             35768            2562183708   
3    BIRMINGHAM             AL             35206            2058330146   
4      MC CALLA             AL             35111            2054776161   

      county submitted_data passed_quality_assurance_check  \
0   Franklin              Y                              Y   
1  Talladega              Y                              Y   
2    Jackson              Y                              Y   
3  Jefferson              N                                  
4  Jefferson              N                                  

  residents_weekly_admissions_covid_19 residents_total_admissions_covid_19  \
0                                    0                                  11   
1                                    0                                   4   
2                                    0                                   2   
3                                    0                                   6   
4                                    0                                   2   

  residents_weekly_confirmed_covid_19 residents_total_confirmed_covid_19  \
0                                   0                                 60   
1                                   0                                 60   
2                                   0                                 13   
3                                   0                                107   
4                                   0                                 60   

  residents_weekly_all_deaths residents_total_all_deaths  \
0                           2                         36   
1                           0                          5   
2                           0                         31   
3                           0                         20   
4                           0                        113   

  residents_weekly_covid_19_deaths residents_total_covid_19_deaths  \
0                                0                               5   
1                                0                               2   
2                                0                               3   
3                                0                               2   
4                                0                               0   

  number_of_all_beds total_number_of_occupied_beds  \
0                 57                            54   
1                 85                            79   
2                 50                            37   
3                 90                            77   
4                103                            86   

  staff_weekly_confirmed_covid_19 staff_total_confirmed_covid_19  \
0                               0                             61   
1                               0                            108   
2                               0                             52   
3                               0                            116   
4                               0                             31   

  staff_weekly_covid

In [216]:
nh_latest.tail()


week_ending federal_provider_number  \
15125  2022-11-27                  745003   
15126  2022-11-27                  745004   
15127  2022-11-27                  745005   
15128  2022-11-27                  745006   
15129  2022-11-27                  745017   

                                  provider_name          provider_address  \
15125                    NEURORESTORATIVE TEXAS      2301 W. CAMPBELL RD.   
15126              THE BRIXTON AT HORSESHOE BAY        15101 WEST FM 2147   
15127                        CENTER AT ZARAGOZA  12660 PEBBLE HILLS BLVD.   
15128    FIVE POINTS NURSING AND REHABILITATION       1901 N. HAMPTON RD.   
15129  THE LODGE OF SAGINAW HEALTH AND WELLNESS        848 W MCLEROY BLVD   

       provider_city provider_state provider_zip_code provider_phone_number  \
15125        GARLAND             TX             75044            5124382630   
15126  HORSESHOE BAY             TX             78657            7135531321   
15127        EL PASO             TX             79938            9159901700   
15128         DESOTO             TX             75115            9726949810   
15129        SAGINAW             TX             76179            6859001210   

        county submitted_data passed_quality_assurance_check  \
15125   Dallas              N                                  
15126   Burnet              Y                              Y   
15127  El Paso              Y                              Y   
15128   Dallas              Y                              Y   
15129  Tarrant              Y                              Y   

      residents_weekly_admissions_covid_19  \
15125                                    0   
15126                                    1   
15127                                    0   
15128                                    0   
15129                                    0   

      residents_total_admissions_covid_19 residents_weekly_confirmed_covid_19  \
15125                                   0                                   0   
15126                                   1                                   0   
15127                                   8                                   0   
15128                                   0                                   0   
15129                                   0                                   0   

      residents_total_confirmed_covid_19 residents_weekly_all_deaths  \
15125                                  0                           0   
15126                                 10                           0   
15127                                  9                           0   
15128                                 23                           0   
15129                                  0                           0   

      residents_total_all_deaths residents_weekly_covid_19_deaths  \
15125                          0                                0   
15126                          0                                0   
15127                          0                                0   
15128                          8                                0   
15129                          1                                0   

      residents_total_covid_19_deaths number_of_all_beds  \
15125                               0                 12   
15126                               0                120   
15127                               0                 80   
15128                               1                120   
15129                               0                130   

      total_number_of_occupied_beds staff_weekly_confirmed_covid_19  \
15125                             1                               0   
15126                            48                               0   
15127                            26                               0   
15128                            81                               0   
15129                            40                               0   

      staff_

In [217]:

list(nh_latest.columns)

['week_ending',
 'federal_provider_number',
 'provider_name',
 'provider_address',
 'provider_city',
 'provider_state',
 'provider_zip_code',
 'provider_phone_number',
 'county',
 'submitted_data',
 'passed_quality_assurance_check',
 'residents_weekly_admissions_covid_19',
 'residents_total_admissions_covid_19',
 'residents_weekly_confirmed_covid_19',
 'residents_total_confirmed_covid_19',
 'residents_weekly_all_deaths',
 'residents_total_all_deaths',
 'residents_weekly_covid_19_deaths',
 'residents_total_covid_19_deaths',
 'number_of_all_beds',
 'total_number_of_occupied_beds',
 'staff_weekly_confirmed_covid_19',
 'staff_total_confirmed_covid_19',
 'staff_weekly_covid_19_deaths',
 'staff_total_covid_19_deaths',
 'Staff_Shortage',
 'shortage_of_nursing_staff',
 'shortage_of_clinical_staff',
 'shortage_of_aides',
 'shortage_of_other_staff',
 'weekly_resident_confirmed_covid_19_cases_per_1_000_residents',
 'weekly_resident_covid_19_deaths_per_1_000_residents',
 'total_resident_confirmed_

In [149]:
nh_latest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15130 entries, 0 to 15129
Columns: 121 entries, week_ending to Percentage_of_Current_Healthcare_Personnel_with_a_Completed_Vaccination_Up_to_Date_with_COVID_19_Vaccines
dtypes: object(121)
memory usage: 14.0+ MB


In [150]:
# from df, keep only needed cols
needed_cols = [
                'week_ending','federal_provider_number','provider_name','provider_address',
                'provider_city','provider_state','provider_zip_code','provider_phone_number',
                'county','submitted_data','passed_quality_assurance_check','residents_weekly_confirmed_covid_19',
                'residents_weekly_all_deaths','residents_weekly_covid_19_deaths',
                'number_of_all_beds','total_number_of_occupied_beds',
                'staff_weekly_confirmed_covid_19',
                'staff_weekly_covid_19_deaths',
                'shortage_of_nursing_staff',
                'shortage_of_clinical_staff',
                'shortage_of_aides',
                'weekly_resident_confirmed_covid_19_cases_per_1_000_residents',
                'number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result',
                'number_of_residents_with_new_influenza',
                'number_of_staff_and_or_personnel_with_new_influenza',
                'Able_to_Test_or_Obtain_Resources_to_Test_All_Residents_Staff_and_or_Personnel',
                'therapeutic_bamlanivimab_number_of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_bamlanivimab_number_of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_casirivimab_plus_imdevimab_number_of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_casirivimab_plus_imdevimab_number_of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_bamlanivimab_plus_etesevimab_number_of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_bamlanivimab_plus_etesevimab_number_of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_sotrovimab_number_of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_sotrovimab_number_of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_evusheld_number_of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_evusheld_number_of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_molnupiravir_number_ of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_molnupiravir_number_ of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_paxlovid_number_ of_residents_treated_from_stock_stored_at_this_facility',
                 'therapeutic_paxlovid_number_ of_residents_treated_from_stock_stored_at_another_facility',
                 'therapeutic_bebtelovimab_number_of_residents_treated from_stock_stored_at_this_facility',
                 'therapeutic_bebtelovimab_number_of_residents_treated from_stock_stored_at_another_facility',
                'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week',
                'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time',
                'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time',
                'recent_percentage_of_current_residents_who_received_a_completed_covid_19_vaccination_at_any_time',
                'percentage_of_current_residents_who_received_a_completed_covid_19_vaccination_at_any_time',
                'percentage_of_current_residents_with_no_medical_contraindications_who_received_a_completed_covid_19_vaccination_at_any_time',
                'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week',
                'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time',
                'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time',
                'percentage_of_current_healthcare_personnel_who_received_a_completed_covid_19_vaccination_at_any_time',
                'percentage_of_current_healthcare_personnel_with_no_medical_contraindications_who_received_a_completed_covid_19_vaccination_at_any_time',
                'recent_percentage_of_current_healthcare_personnel_who_received_a_completed_covid_19_vaccination_at_any_time'
                'number_of_residents_with_a_completed_vaccination_staying_in_this_facility_for_at_least_1_day_this_week_who_received_a_covid_19_vaccine_booster_at_any_time',
                'recent_percentage_of_current_residents_with_a_completed_vaccination_who_received_a_covid_19_vaccine_booster_at_any_time',
                'percentage_of_current_residents_with_a_completed_vaccination_who_received_a_covid_19_vaccine_booster_at_any_time',
                'Number_of_Residents_Staying_in_this_Facility_for_At_Least_1_Day_This_Week_Up_to_Date_with_COVID_19_Vaccines',
                'Recent_Percentage_of_Current_Residents_Up_to_Date_with_COVID_19_Vaccines',
                'Percentage_of_Current_Residents_Up_to_Date_with_COVID_19_Vaccines',
                'number_of_healthcare_personnel_with_a_completed_vaccination_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_received_a_covid_19_vaccine_booster_at_any_time',
                'recent_percentage_of_current_healthcare_personnel_with_a_completed_vaccination_who_received_a_covid_19_vaccine_booster_at_any_time',
                'percentage_of_current_healthcare_personnel_with_a_completed_vaccination_who_received_a_covid_19_vaccine_booster_at_any_time',
                'Number_of_Healthcare_Personnel_Eligible_to_Work_in_this_Facility_for_At_Least_1_Day_This_Week_Up_to_Date_with_COVID_19_Vaccines',
                'Recent_Percentage_of_Current_Healthcare_Personnel_Up_to_Date_with_COVID_19_Vaccines',
                'Percentage_of_Current_Healthcare_Personnel_Up_to_Date_with_COVID_19_Vaccines',
                'Percentage_of_Current_Healthcare_Personnel_with_a_Completed_Vaccination_Up_to_Date_with_COVID_19_Vaccines'
                ]

nh_latest = nh_latest[needed_cols]


In [151]:
nh_latest.head()

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   

                                 provider_name             provider_address  \
0                     BURNS NURSING HOME, INC.         701 MONROE STREET NW   
1               COOSA VALLEY HEALTHCARE CENTER       260 WEST WALNUT STREET   
2                   HIGHLANDS HEALTH AND REHAB          380 WOODS COVE ROAD   
3  EASTVIEW REHABILITATION & HEALTHCARE CENTER     7755 FOURTH AVENUE SOUTH   
4                PLANTATION MANOR NURSING HOME  6450 OLD TUSCALOOSA HIGHWAY   

  provider_city provider_state provider_zip_code provider_phone_number  \
0  RUSSELLVILLE             AL             35653            2563324110   
1     SYLACAUGA             AL             35150            2562495604   
2    SCOTTSBORO             AL             35768            2562183708   
3    BIRMINGHAM             AL             35206            2058330146   
4      MC CALLA             AL             35111            2054776161   

      county submitted_data passed_quality_assurance_check  \
0   Franklin              Y                              Y   
1  Talladega              Y                              Y   
2    Jackson              Y                              Y   
3  Jefferson              N                                  
4  Jefferson              N                                  

  residents_weekly_confirmed_covid_19 residents_weekly_all_deaths  \
0                                   0                           2   
1                                   0                           0   
2                                   0                           0   
3                                   0                           0   
4                                   0                           0   

  residents_weekly_covid_19_deaths number_of_all_beds  \
0                                0                 57   
1                                0                 85   
2                                0                 50   
3                                0                 90   
4                                0                103   

  total_number_of_occupied_beds staff_weekly_confirmed_covid_19  \
0                            54                               0   
1                            79                               0   
2                            37                               0   
3                            77                               0   
4                            86                               0   

  shortage_of_nursing_staff shortage_of_clinical_staff shortage_of_aides  \
0                                                                          
1                                                                          
2                                                                          
3                                                                          
4                                                                          

  weekly_resident_confirmed_covid_19_cases_per_1_000_residents  \
0                                                  0             
1                                                  0             
2                                                  0             
3                                                  0             
4                                                  0             

  number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result  \
0                                                  0                          
1                                                  0                          
2                                                  0                          
3                                                                             
4                                                   

In [152]:
#read in parquet file with latest date of all data prior to most recent data get
nh_old=pd.read_parquet('data/nh_all.parquet.gzip')

In [153]:
#concat new with old save to a new df with date as last week start date
nh_all = pd.concat([nh_latest, nh_old]).reset_index(drop=True)

In [154]:
if len(nh_all) == len(nh_old) + len(nh_latest):
    print('proceed')
else:
    print('gtfo')

proceed


In [155]:
nh_all.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1139524 entries, 0 to 1139523
Data columns (total 32 columns):
 #   Column                                                                                                                                                          Non-Null Count    Dtype 
---  ------                                                                                                                                                          --------------    ----- 
 0   week_ending                                                                                                                                                     1139524 non-null  object
 1   federal_provider_number                                                                                                                                         1139524 non-null  object
 2   provider_name                                                                                                             

In [156]:
nh_all.sort_values(by=['week_ending']).head()

week_ending federal_provider_number                 provider_name  \
302712  2021-06-27                  015009      BURNS NURSING HOME, INC.   
312876  2021-06-27                  365937  OHMAN FAMILY LIVING AT BRIAR   
312877  2021-06-27                  365939    EDGEWOOD MANOR OF WELLSTON   
312878  2021-06-27                  365940     AUTUMN AEGIS NURSING HOME   
312879  2021-06-27                  365943   EUCLID SUBACUTE CARE CENTER   

             provider_address provider_city provider_state provider_zip_code  \
302712   701 MONROE STREET NW  RUSSELLVILLE             AL             35653   
312876        15950 PIERCE ST   MIDDLEFIELD             OH             44062   
312877  405 NORTH PARK AVENUE      WELLSTON             OH             45692   
312878        1130 TOWER BLVD        LORAIN             OH             44052   
312879  18901 LAKE SHORE BLVD        EUCLID             OH             44119   

       provider_phone_number    county submitted_data  \
302712            2563324110  Franklin              Y   
312876            4406325241    Geauga              Y   
312877            7403845611   Jackson              Y   
312878            4402826768    Lorain              Y   
312879            2166928810  Cuyahoga              Y   

       passed_quality_assurance_check residents_weekly_confirmed_covid_19  \
302712                              Y                                   0   
312876                              Y                                   0   
312877                              Y                                   0   
312878                              Y                                   0   
312879                              Y                                   0   

       residents_weekly_all_deaths residents_weekly_covid_19_deaths  \
302712                           0                                0   
312876                           0                                0   
312877                           0                                0   
312878                           1                                0   
312879                           0                                0   

       number_of_all_beds total_number_of_occupied_beds  \
302712                 57                            54   
312876                 96                            81   
312877                 50                            38   
312878                 99                            64   
312879                 40                            32   

       staff_weekly_confirmed_covid_19 shortage_of_nursing_staff  \
302712                               0                         N   
312876                               0                         N   
312877                               0                         N   
312878                               0                         N   
312879                               0                         N   

       shortage_of_clinical_staff shortage_of_aides  \
302712                          N                 N   
312876                          N                 N   
312877                          N                 N   
312878                          N                 N   
312879                          N                 N   

       weekly_resident_confirmed_covid_19_cases_per_1_000_residents  \
302712                                                  0             
312876                                                  0             
312877                                                  0             
312878                                                  0             
312879                                                  0             

       number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result  \
302712                                                  0                          
312876                                                  0                          
312877                                                  0     

In [157]:
nh_all.sort_values(by=['week_ending']).tail()

week_ending federal_provider_number               provider_name  \
10081  2022-11-27                  365976      PROVIDENCE CARE CENTER   
10080  2022-11-27                  365975          PARK HEALTH CENTER   
10079  2022-11-27                  365974  OHIO LIVING QUAKER HEIGHTS   
10091  2022-11-27                  365991   ADDISON HEALTHCARE CENTER   
0      2022-11-27                  015009    BURNS NURSING HOME, INC.   

           provider_address   provider_city provider_state provider_zip_code  \
10081     2025 HAYES AVENUE        SANDUSKY             OH             44870   
10080       100 PINE AVENUE  ST CLAIRSVILLE             OH             43950   
10079  514 WEST HIGH STREET     WAYNESVILLE             OH             45068   
10091  8055 ADDISON ROAD SE          MASURY             OH             44438   
0      701 MONROE STREET NW    RUSSELLVILLE             AL             35653   

      provider_phone_number    county submitted_data  \
10081            4196272273      Erie              Y   
10080            7406954925   Belmont              Y   
10079            5138976050    Warren              Y   
10091            3304482547  Trumbull              Y   
0                2563324110  Franklin              Y   

      passed_quality_assurance_check residents_weekly_confirmed_covid_19  \
10081                              Y                                  19   
10080                              Y                                   0   
10079                              Y                                   0   
10091                              Y                                   0   
0                                  Y                                   0   

      residents_weekly_all_deaths residents_weekly_covid_19_deaths  \
10081                           1                                1   
10080                           0                                0   
10079                           1                                0   
10091                           0                                0   
0                               2                                0   

      number_of_all_beds total_number_of_occupied_beds  \
10081                138                            92   
10080                 87                            82   
10079                 70                            47   
10091                 64                            48   
0                     57                            54   

      staff_weekly_confirmed_covid_19 shortage_of_nursing_staff  \
10081                              16                         Y   
10080                               0                             
10079                               0                             
10091                               0                             
0                                   0                             

      shortage_of_clinical_staff shortage_of_aides  \
10081                          N                 Y   
10080                                                
10079                                                
10091                                                
0                                                    

      weekly_resident_confirmed_covid_19_cases_per_1_000_residents  \
10081                                             206.52             
10080                                                  0             
10079                                                  0             
10091                                                  0             
0                                                      0             

      number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result  \
10081                                                 16                          
10080                                                  0                          
10079                                                  0                          
10091                                    

In [158]:
#send updated nh_all df to parquet
nh_all.to_parquet('data/nh_all.parquet.gzip', compression='gzip')

In [159]:
#check for dup rows
nh_all.loc[nh_all.duplicated(),]

Empty DataFrame
Columns: [week_ending, federal_provider_number, provider_name, provider_address, provider_city, provider_state, provider_zip_code, provider_phone_number, county, submitted_data, passed_quality_assurance_check, residents_weekly_confirmed_covid_19, residents_weekly_all_deaths, residents_weekly_covid_19_deaths, number_of_all_beds, total_number_of_occupied_beds, staff_weekly_confirmed_covid_19, shortage_of_nursing_staff, shortage_of_clinical_staff, shortage_of_aides, weekly_resident_confirmed_covid_19_cases_per_1_000_residents, number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result, number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week, number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time, number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time, percentage_of_current_residents_who_received_a_completed_covid_19_vaccination_at_any_time, percentage_of_current_residents_with_no_medical_contraindications_who_received_a_completed_covid_19_vaccination_at_any_time, number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week, number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time, number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time, percentage_of_current_healthcare_personnel_who_received_a_completed_covid_19_vaccination_at_any_time, percentage_of_current_healthcare_personnel_with_no_medical_contraindications_who_received_a_completed_covid_19_vaccination_at_any_time]
Index: []

In [160]:
# rename long cols
nh_all = nh_all.rename({
    'provider_zip_code':'provider_zip',
    'passed_quality_assurance_check':'data_passed_qa',
    'residents_weekly_confirmed_covid_19':'res_wk_confirmed_c19',
    'number_of_all_beds':'num_all_beds',
    'total_number_of_occupied_beds':'num_occ_beds',
    'shortage_of_nursing_staff':'short_nrsg_staff',
    'shortage_of_aides':'short_aides',
    'weekly_resident_confirmed_covid_19_cases_per_1_000_residents':'wk_res_confirmed_c19_cases_per_1000',
    'number_of_staff_and_or_personnel_with_a_new_positive_covid_19_test_result':'num_staff_new_pos_c19_test',
    'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week':'num_res_in_facility',
    'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time':'num_res_comp_c19_vax',
    'number_of_residents_staying_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time':'num_res_offered_declined_cvd_vax',
    'percentage_of_current_residents_who_received_a_completed_covid_19_vaccination_at_any_time':'pct_res_comp_c19_vax',
    'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week':'num_hcp',
    'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_received_a_completed_covid_19_vaccination_at_any_time':'num_hcp_comp_c19_vax',
    'number_of_all_healthcare_personnel_eligible_to_work_in_this_facility_for_at_least_1_day_this_week_who_were_offered_but_declined_a_covid_19_vaccine_at_any_time':'num_hcp_offered_declined_c19_vax',
    'percentage_of_current_healthcare_personnel_who_received_a_completed_covid_19_vaccination_at_any_time': 'pct_hcp_comp_c19_vax'
   }, axis=1)

In [161]:
nh_all.head()

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   

                                 provider_name             provider_address  \
0                     BURNS NURSING HOME, INC.         701 MONROE STREET NW   
1               COOSA VALLEY HEALTHCARE CENTER       260 WEST WALNUT STREET   
2                   HIGHLANDS HEALTH AND REHAB          380 WOODS COVE ROAD   
3  EASTVIEW REHABILITATION & HEALTHCARE CENTER     7755 FOURTH AVENUE SOUTH   
4                PLANTATION MANOR NURSING HOME  6450 OLD TUSCALOOSA HIGHWAY   

  provider_city provider_state provider_zip provider_phone_number     county  \
0  RUSSELLVILLE             AL        35653            2563324110   Franklin   
1     SYLACAUGA             AL        35150            2562495604  Talladega   
2    SCOTTSBORO             AL        35768            2562183708    Jackson   
3    BIRMINGHAM             AL        35206            2058330146  Jefferson   
4      MC CALLA             AL        35111            2054776161  Jefferson   

  submitted_data data_passed_qa res_wk_confirmed_c19  \
0              Y              Y                    0   
1              Y              Y                    0   
2              Y              Y                    0   
3              N                                   0   
4              N                                   0   

  residents_weekly_all_deaths residents_weekly_covid_19_deaths num_all_beds  \
0                           2                                0           57   
1                           0                                0           85   
2                           0                                0           50   
3                           0                                0           90   
4                           0                                0          103   

  num_occ_beds staff_weekly_confirmed_covid_19 short_nrsg_staff  \
0           54                               0                    
1           79                               0                    
2           37                               0                    
3           77                               0                    
4           86                               0                    

  shortage_of_clinical_staff short_aides wk_res_confirmed_c19_cases_per_1000  \
0                                                                          0   
1                                                                          0   
2                                                                          0   
3                                                                          0   
4                                                                          0   

  num_staff_new_pos_c19_test num_res_in_facility num_res_comp_c19_vax  \
0                          0                  53                   49   
1                          0                  78                   70   
2                          0                                            
3                                                                       
4                                                                       

  num_res_offered_declined_cvd_vax pct_res_comp_c19_vax  \
0                                4               92.453   
1                                7               89.744   
2                                                         
3                                                         
4                                                         

  percentage_of_current_residents_with_no_medical_contraindications_who_received_a_completed_covid_19_vaccination_at_any_time  \
0                                             92.453                                                                            
1                                             89.74

In [162]:
# subset cols
nh_sub = nh_all[['week_ending','federal_provider_number', 'provider_name', 'provider_address', 'provider_city', 'provider_state', 'provider_zip', 'provider_phone_number', 'county', 'submitted_data','data_passed_qa','num_all_beds','num_occ_beds','short_nrsg_staff','short_aides','res_wk_confirmed_c19','wk_res_confirmed_c19_cases_per_1000','num_staff_new_pos_c19_test','num_res_in_facility','num_res_comp_c19_vax','num_res_offered_declined_cvd_vax','pct_res_comp_c19_vax','num_hcp','num_hcp_comp_c19_vax','num_hcp_offered_declined_c19_vax','pct_hcp_comp_c19_vax']]

nh_sub.head()

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   

                                 provider_name             provider_address  \
0                     BURNS NURSING HOME, INC.         701 MONROE STREET NW   
1               COOSA VALLEY HEALTHCARE CENTER       260 WEST WALNUT STREET   
2                   HIGHLANDS HEALTH AND REHAB          380 WOODS COVE ROAD   
3  EASTVIEW REHABILITATION & HEALTHCARE CENTER     7755 FOURTH AVENUE SOUTH   
4                PLANTATION MANOR NURSING HOME  6450 OLD TUSCALOOSA HIGHWAY   

  provider_city provider_state provider_zip provider_phone_number     county  \
0  RUSSELLVILLE             AL        35653            2563324110   Franklin   
1     SYLACAUGA             AL        35150            2562495604  Talladega   
2    SCOTTSBORO             AL        35768            2562183708    Jackson   
3    BIRMINGHAM             AL        35206            2058330146  Jefferson   
4      MC CALLA             AL        35111            2054776161  Jefferson   

  submitted_data data_passed_qa num_all_beds num_occ_beds short_nrsg_staff  \
0              Y              Y           57           54                    
1              Y              Y           85           79                    
2              Y              Y           50           37                    
3              N                          90           77                    
4              N                         103           86                    

  short_aides res_wk_confirmed_c19 wk_res_confirmed_c19_cases_per_1000  \
0                                0                                   0   
1                                0                                   0   
2                                0                                   0   
3                                0                                   0   
4                                0                                   0   

  num_staff_new_pos_c19_test num_res_in_facility num_res_comp_c19_vax  \
0                          0                  53                   49   
1                          0                  78                   70   
2                          0                                            
3                                                                       
4                                                                       

  num_res_offered_declined_cvd_vax pct_res_comp_c19_vax num_hcp  \
0                                4               92.453      81   
1                                7               89.744     192   
2                                                                 
3                                                                 
4                                                                 

  num_hcp_comp_c19_vax num_hcp_offered_declined_c19_vax pct_hcp_comp_c19_vax  
0                   70                               10                86.42  
1                  155                               33               80.729  
2                                                                             
3                                                                             
4

### revise data types

In [163]:
nh_sub=nh_sub.replace(r'^\s*$', np.nan, regex=True)
nh_sub.head(10)

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   
5  2022-11-27                  015016   
6  2022-11-27                  015019   
7  2022-11-27                  015023   
8  2022-11-27                  015024   
9  2022-11-27                  015027   

                                      provider_name  \
0                          BURNS NURSING HOME, INC.   
1                    COOSA VALLEY HEALTHCARE CENTER   
2                        HIGHLANDS HEALTH AND REHAB   
3       EASTVIEW REHABILITATION & HEALTHCARE CENTER   
4                     PLANTATION MANOR NURSING HOME   
5              ATHENS HEALTH AND REHABILITATION LLC   
6                                  MERRY WOOD LODGE   
7                            HATLEY HEALTH CARE INC   
8  LIMESTONE NURSING AND REHABILITATION CENTER, LLC   
9           WETUMPKA HEALTH AND REHABILITATION, LLC   

              provider_address provider_city provider_state provider_zip  \
0         701 MONROE STREET NW  RUSSELLVILLE             AL        35653   
1       260 WEST WALNUT STREET     SYLACAUGA             AL        35150   
2          380 WOODS COVE ROAD    SCOTTSBORO             AL        35768   
3     7755 FOURTH AVENUE SOUTH    BIRMINGHAM             AL        35206   
4  6450 OLD TUSCALOOSA HIGHWAY      MC CALLA             AL        35111   
5       611 WEST MARKET STREET        ATHENS             AL        35611   
6           280 MT HEBRON ROAD        ELMORE             AL        36025   
7     300 MEDICAL CENTER DRIVE       CLANTON             AL        35045   
8       1600 WEST HOBBS STREET        ATHENS             AL        35611   
9          1825 HOLTVILLE ROAD      WETUMPKA             AL        36092   

  provider_phone_number     county submitted_data data_passed_qa num_all_beds  \
0            2563324110   Franklin              Y              Y           57   
1            2562495604  Talladega              Y              Y           85   
2            2562183708    Jackson              Y              Y           50   
3            2058330146  Jefferson              N            NaN           90   
4            2054776161  Jefferson              N            NaN          103   
5            2562321620  Limestone              Y              Y          149   
6            3345678484     Elmore              N            NaN          124   
7            2057554960    Chilton              Y              Y          201   
8            2562323461  Limestone              Y              Y          170   
9            3345675131     Elmore              Y              Y          121   

  num_occ_beds short_nrsg_staff short_aides res_wk_confirmed_c19  \
0           54              NaN         NaN                    0   
1           79              NaN         NaN                    0   
2           37              NaN         NaN                    0   
3           77              NaN         NaN                    0   
4           86              NaN         NaN                    0   
5          134              NaN         NaN                    0   
6          100              NaN         NaN                    0   
7           84                Y           Y                    0   
8          127              NaN         NaN                   16   
9          116              NaN         NaN                    0   

  wk_res_confirmed_c19_cases_per_1000 num_staff_new_pos_c19_test  \
0                                   0                          0   
1                                   0                          0   
2                                   0                          0   
3                                   0                        NaN   
4                                   0                        NaN   
5                                   0                     

In [164]:
#revise nums to float cols
float_cols = ['num_all_beds','num_occ_beds','res_wk_confirmed_c19','wk_res_confirmed_c19_cases_per_1000','num_staff_new_pos_c19_test','num_res_in_facility','num_res_comp_c19_vax','num_res_offered_declined_cvd_vax','pct_res_comp_c19_vax','num_hcp','num_hcp_comp_c19_vax','num_hcp_offered_declined_c19_vax','pct_hcp_comp_c19_vax']

nh_sub[float_cols]=nh_sub[float_cols].astype('float')

nh_sub['week_ending'] = pd.to_datetime(nh_sub['week_ending'], format='%Y-%m-%d')

# subset to week ending greater than 7-11-21
nh_sub = nh_sub.loc[nh_sub['week_ending']>='2021-07-11']
nh_sub.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 1109017 entries, 0 to 1139523
Data columns (total 26 columns):
 #   Column                               Non-Null Count    Dtype         
---  ------                               --------------    -----         
 0   week_ending                          1109017 non-null  datetime64[ns]
 1   federal_provider_number              1109017 non-null  object        
 2   provider_name                        1109017 non-null  object        
 3   provider_address                     1109017 non-null  object        
 4   provider_city                        1109017 non-null  object        
 5   provider_state                       1109017 non-null  object        
 6   provider_zip                         1109017 non-null  object        
 7   provider_phone_number                1109017 non-null  object        
 8   county                               1109017 non-null  object        
 9   submitted_data                       1109017 non-null  ob

In [165]:
# create week start date col
nh_sub['week_start'] = nh_sub['week_ending'] - timedelta(days=6)

In [166]:
nh_sub['month_year'] = pd.to_datetime(nh_sub['week_start']).dt.to_period('M')
nh_sub.head()

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   

                                 provider_name             provider_address  \
0                     BURNS NURSING HOME, INC.         701 MONROE STREET NW   
1               COOSA VALLEY HEALTHCARE CENTER       260 WEST WALNUT STREET   
2                   HIGHLANDS HEALTH AND REHAB          380 WOODS COVE ROAD   
3  EASTVIEW REHABILITATION & HEALTHCARE CENTER     7755 FOURTH AVENUE SOUTH   
4                PLANTATION MANOR NURSING HOME  6450 OLD TUSCALOOSA HIGHWAY   

  provider_city provider_state provider_zip provider_phone_number     county  \
0  RUSSELLVILLE             AL        35653            2563324110   Franklin   
1     SYLACAUGA             AL        35150            2562495604  Talladega   
2    SCOTTSBORO             AL        35768            2562183708    Jackson   
3    BIRMINGHAM             AL        35206            2058330146  Jefferson   
4      MC CALLA             AL        35111            2054776161  Jefferson   

  submitted_data data_passed_qa  num_all_beds  num_occ_beds short_nrsg_staff  \
0              Y              Y          57.0          54.0              NaN   
1              Y              Y          85.0          79.0              NaN   
2              Y              Y          50.0          37.0              NaN   
3              N            NaN          90.0          77.0              NaN   
4              N            NaN         103.0          86.0              NaN   

  short_aides  res_wk_confirmed_c19  wk_res_confirmed_c19_cases_per_1000  \
0         NaN                   0.0                                  0.0   
1         NaN                   0.0                                  0.0   
2         NaN                   0.0                                  0.0   
3         NaN                   0.0                                  0.0   
4         NaN                   0.0                                  0.0   

   num_staff_new_pos_c19_test  num_res_in_facility  num_res_comp_c19_vax  \
0                         0.0                 53.0                  49.0   
1                         0.0                 78.0                  70.0   
2                         0.0                  NaN                   NaN   
3                         NaN                  NaN                   NaN   
4                         NaN                  NaN                   NaN   

   num_res_offered_declined_cvd_vax  pct_res_comp_c19_vax  num_hcp  \
0                               4.0                92.453     81.0   
1                               7.0                89.744    192.0   
2                               NaN                   NaN      NaN   
3                               NaN                   NaN      NaN   
4                               NaN                   NaN      NaN   

   num_hcp_comp_c19_vax  num_hcp_offered_declined_c19_vax  \
0                  70.0                              10.0   
1                 155.0                              33.0   
2                   NaN                               NaN   
3                   NaN                               NaN   
4                   NaN                               NaN   

   pct_hcp_comp_c19_vax week_start month_year  
0                86.420 2022-11-21    2022-11  
1                80.729 2022-11-21    2022-11  
2                   NaN 2022-11-21    2022-11  
3                   NaN 2022-11-21    2022-11  
4                   NaN 2022-11-21    2022-11

In [167]:
nh_sub.head(10)

week_ending federal_provider_number  \
0  2022-11-27                  015009   
1  2022-11-27                  015010   
2  2022-11-27                  015012   
3  2022-11-27                  015014   
4  2022-11-27                  015015   
5  2022-11-27                  015016   
6  2022-11-27                  015019   
7  2022-11-27                  015023   
8  2022-11-27                  015024   
9  2022-11-27                  015027   

                                      provider_name  \
0                          BURNS NURSING HOME, INC.   
1                    COOSA VALLEY HEALTHCARE CENTER   
2                        HIGHLANDS HEALTH AND REHAB   
3       EASTVIEW REHABILITATION & HEALTHCARE CENTER   
4                     PLANTATION MANOR NURSING HOME   
5              ATHENS HEALTH AND REHABILITATION LLC   
6                                  MERRY WOOD LODGE   
7                            HATLEY HEALTH CARE INC   
8  LIMESTONE NURSING AND REHABILITATION CENTER, LLC   
9           WETUMPKA HEALTH AND REHABILITATION, LLC   

              provider_address provider_city provider_state provider_zip  \
0         701 MONROE STREET NW  RUSSELLVILLE             AL        35653   
1       260 WEST WALNUT STREET     SYLACAUGA             AL        35150   
2          380 WOODS COVE ROAD    SCOTTSBORO             AL        35768   
3     7755 FOURTH AVENUE SOUTH    BIRMINGHAM             AL        35206   
4  6450 OLD TUSCALOOSA HIGHWAY      MC CALLA             AL        35111   
5       611 WEST MARKET STREET        ATHENS             AL        35611   
6           280 MT HEBRON ROAD        ELMORE             AL        36025   
7     300 MEDICAL CENTER DRIVE       CLANTON             AL        35045   
8       1600 WEST HOBBS STREET        ATHENS             AL        35611   
9          1825 HOLTVILLE ROAD      WETUMPKA             AL        36092   

  provider_phone_number     county submitted_data data_passed_qa  \
0            2563324110   Franklin              Y              Y   
1            2562495604  Talladega              Y              Y   
2            2562183708    Jackson              Y              Y   
3            2058330146  Jefferson              N            NaN   
4            2054776161  Jefferson              N            NaN   
5            2562321620  Limestone              Y              Y   
6            3345678484     Elmore              N            NaN   
7            2057554960    Chilton              Y              Y   
8            2562323461  Limestone              Y              Y   
9            3345675131     Elmore              Y              Y   

   num_all_beds  num_occ_beds short_nrsg_staff short_aides  \
0          57.0          54.0              NaN         NaN   
1          85.0          79.0              NaN         NaN   
2          50.0          37.0              NaN         NaN   
3          90.0          77.0              NaN         NaN   
4         103.0          86.0              NaN         NaN   
5         149.0         134.0              NaN         NaN   
6         124.0         100.0              NaN         NaN   
7         201.0          84.0                Y           Y   
8         170.0         127.0              NaN         NaN   
9         121.0         116.0              NaN         NaN   

   res_wk_confirmed_c19  wk_res_confirmed_c19_cases_per_1000  \
0                   0.0                                 0.00   
1                   0.0                                 0.00   
2                   0.0                                 0.00   
3                   0.0                                 0.00   
4                   0.0                                 0.00   
5                   0.0                                 0.00   
6                   0.0                                 0.00   
7                   0.0                                 0.00   
8                  16.0                               125.98   
9                   0.0            

In [168]:
nh_sub.data_passed_qa.value_counts()

Y    1087251
N      12994
Name: data_passed_qa, dtype: int64

In [169]:
nh_dq_fail=nh_sub.loc[nh_sub['data_passed_qa']=='N']
nh_dq_fail.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 12994 entries, 266 to 1139521
Data columns (total 28 columns):
 #   Column                               Non-Null Count  Dtype         
---  ------                               --------------  -----         
 0   week_ending                          12994 non-null  datetime64[ns]
 1   federal_provider_number              12994 non-null  object        
 2   provider_name                        12994 non-null  object        
 3   provider_address                     12994 non-null  object        
 4   provider_city                        12994 non-null  object        
 5   provider_state                       12994 non-null  object        
 6   provider_zip                         12994 non-null  object        
 7   provider_phone_number                12994 non-null  object        
 8   county                               12994 non-null  object        
 9   submitted_data                       12994 non-null  object        
 10  data_p

In [170]:
nh_dq_fail.provider_name.value_counts().sort_index()

ABBY GARDENS HEALTHCARE CENTER                         1
ABCM REHAB CENTERS OF INDEPENDENCE EAST CAMPUS         9
ABERNETHY LAURELS                                      1
ABINGTON CREST HEALTHCAREANDREHABILITATION CENTER      1
ABRAMSON SENIOR CARE AT LANKENAU MEDICAL CENTER        5
ACCEL AT CRYSTAL PARK                                 53
ACCELA REHAB AND CARE CENTER AT SOMERTON               1
ACCORDIUS HEALTH AT BREVARD                            1
ACCORDIUS HEALTH AT CHARLOTTE                          2
ACCORDIUS HEALTH AT CONCORD                            1
ACCORDIUS HEALTH AT GASTONIA                           1
ACCORDIUS HEALTH AT HENDERSONVILLE LLC                 4
ACCORDIUS HEALTH AT ROSE MANOR LLC                     1
ACCORDIUS HEALTH AT STATESVILLE                        3
ACCORDIUS HEALTH AT WILMINGTON                         1
ACCURA HEALTHCARE OF SHENANDOAH                        1
ADVANCED CARE CENTER                                   2
ADVANCED HEALTH & REHAB CENTER 

In [171]:
nh_dq_pass=nh_sub.loc[nh_sub['data_passed_qa']=='Y']
nh_dq_pass.head()

week_ending federal_provider_number                         provider_name  \
0  2022-11-27                  015009              BURNS NURSING HOME, INC.   
1  2022-11-27                  015010        COOSA VALLEY HEALTHCARE CENTER   
2  2022-11-27                  015012            HIGHLANDS HEALTH AND REHAB   
5  2022-11-27                  015016  ATHENS HEALTH AND REHABILITATION LLC   
7  2022-11-27                  015023                HATLEY HEALTH CARE INC   

           provider_address provider_city provider_state provider_zip  \
0      701 MONROE STREET NW  RUSSELLVILLE             AL        35653   
1    260 WEST WALNUT STREET     SYLACAUGA             AL        35150   
2       380 WOODS COVE ROAD    SCOTTSBORO             AL        35768   
5    611 WEST MARKET STREET        ATHENS             AL        35611   
7  300 MEDICAL CENTER DRIVE       CLANTON             AL        35045   

  provider_phone_number     county submitted_data data_passed_qa  \
0            2563324110   Franklin              Y              Y   
1            2562495604  Talladega              Y              Y   
2            2562183708    Jackson              Y              Y   
5            2562321620  Limestone              Y              Y   
7            2057554960    Chilton              Y              Y   

   num_all_beds  num_occ_beds short_nrsg_staff short_aides  \
0          57.0          54.0              NaN         NaN   
1          85.0          79.0              NaN         NaN   
2          50.0          37.0              NaN         NaN   
5         149.0         134.0              NaN         NaN   
7         201.0          84.0                Y           Y   

   res_wk_confirmed_c19  wk_res_confirmed_c19_cases_per_1000  \
0                   0.0                                  0.0   
1                   0.0                                  0.0   
2                   0.0                                  0.0   
5                   0.0                                  0.0   
7                   0.0                                  0.0   

   num_staff_new_pos_c19_test  num_res_in_facility  num_res_comp_c19_vax  \
0                         0.0                 53.0                  49.0   
1                         0.0                 78.0                  70.0   
2                         0.0                  NaN                   NaN   
5                         0.0                135.0                 115.0   
7                         0.0                 84.0                  83.0   

   num_res_offered_declined_cvd_vax  pct_res_comp_c19_vax  num_hcp  \
0                               4.0                92.453     81.0   
1                               7.0                89.744    192.0   
2                               NaN                   NaN      NaN   
5                              17.0                85.185    253.0   
7                               0.0                98.810    128.0   

   num_hcp_comp_c19_vax  num_hcp_offered_declined_c19_vax  \
0                  70.0                              10.0   
1                 155.0                              33.0   
2                   NaN                               NaN   
5                 183.0                              56.0   
7                 112.0                              13.0   

   pct_hcp_comp_c19_vax week_start month_year  
0                86.420 2022-11-21    2022-11  
1                80.729 2022-11-21    2022-11  
2                   NaN 2022-11-21    2022-11  
5                72.332 2022-11-21    2022-11  
7                87.500 2022-11-21    2022-11

In [172]:
nh_dq_pass.tail()

week_ending federal_provider_number  \
1139515  2022-07-10                  676499   
1139516  2022-07-10                  686123   
1139517  2022-07-10                  686124   
1139518  2022-07-10                  745000   
1139519  2022-07-10                  745001   

                                          provider_name  \
1139515  SPRINGTOWN PARK REHABILITATION AND CARE CENTER   
1139516  KENDALL LAKES HEALTH AND REHABILITATION CENTER   
1139517                           HARMONY HEALTH CENTER   
1139518                          LAS ALTURAS DE PENITAS   
1139519                         ESTATES AT SHAVANO PARK   

              provider_address provider_city provider_state provider_zip  \
1139515  201 WILLIAMS WARD RD.    SPRINGTOWN             TX        76082   
1139516     5280 SW 157 AVENUE         MIAMI             FL        33185   
1139517   9820 N KENDALL DRIVE         MIAMI             FL        33176   
1139518      414 LIBERTY BLVD.       PENITAS             TX        78576   
1139519    4366 LOCKHILL SELMA  SHAVANO PARK             TX        78249   

        provider_phone_number      county submitted_data data_passed_qa  \
1139515            5124382630      Parker              Y              Y   
1139516            7864337400  Miami-Dade              Y              Y   
1139517            3052716311  Miami-Dade              Y              Y   
1139518            9569970800     Hidalgo              Y              Y   
1139519            5124382630       Bexar              Y              Y   

         num_all_beds  num_occ_beds short_nrsg_staff short_aides  \
1139515         120.0          92.0                Y           Y   
1139516         150.0         150.0              NaN         NaN   
1139517         203.0         198.0              NaN         NaN   
1139518         130.0          60.0              NaN         NaN   
1139519         112.0          31.0              NaN         NaN   

         res_wk_confirmed_c19  wk_res_confirmed_c19_cases_per_1000  \
1139515                   1.0                                10.87   
1139516                   0.0                                 0.00   
1139517                   1.0                                 5.05   
1139518                   1.0                                16.67   
1139519                   0.0                                 0.00   

         num_staff_new_pos_c19_test  num_res_in_facility  \
1139515                         0.0                104.0   
1139516                         1.0                149.0   
1139517                         0.0                198.0   
1139518                         2.0                  NaN   
1139519                         0.0                 31.0   

         num_res_comp_c19_vax  num_res_offered_declined_cvd_vax  \
1139515                  84.0                              20.0   
1139516                 115.0                              32.0   
1139517                 159.0                              37.0   
1139518                   NaN                               NaN   
1139519                  30.0                               1.0   

         pct_res_comp_c19_vax  num_hcp  num_hcp_comp_c19_vax  \
1139515                80.769     91.0                  84.0   
1139516                77.181    266.0                 248.0   
1139517                80.303    224.0                 205.0   
1139518                   NaN      NaN                   NaN   
1139519                96.774     83.0                  79.0   

         num_hcp_offered_declined_c19_vax  pct_hcp_comp_c19_vax week_start  \
1139515                               7.0                92.308 2022-07-04   
1139516                              15.0                93.233 2022-07-04   
1139517                              14.0                91.518 2022-07-04   
1139518                               NaN                   NaN 2022-07-04   
1139519                               4.0                95.181 2022-07-04   

        month_

In [173]:
nh_dq_pass.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1087251 entries, 0 to 1139519
Data columns (total 28 columns):
 #   Column                               Non-Null Count    Dtype         
---  ------                               --------------    -----         
 0   week_ending                          1087251 non-null  datetime64[ns]
 1   federal_provider_number              1087251 non-null  object        
 2   provider_name                        1087251 non-null  object        
 3   provider_address                     1087251 non-null  object        
 4   provider_city                        1087251 non-null  object        
 5   provider_state                       1087251 non-null  object        
 6   provider_zip                         1087251 non-null  object        
 7   provider_phone_number                1087251 non-null  object        
 8   county                               1087251 non-null  object        
 9   submitted_data                       1087251 non-null  ob

In [174]:
#subset to ky
nh_ky=nh_sub.loc[nh_sub['provider_state']=='KY']
nh_ky.head()

week_ending federal_provider_number  \
4893  2022-11-27                  185003   
4894  2022-11-27                  185005   
4895  2022-11-27                  185006   
4896  2022-11-27                  185008   
4897  2022-11-27                  185012   

                                          provider_name  \
4893                LAUREL HEIGHTS HOME FOR THE ELDERLY   
4894  SPRING CREEK POST-ACUTE AND REHABILITATION CENTER   
4895            MORGANTOWN CARE & REHABILITATION CENTER   
4896  OWENSBORO HEALTH MUHLENBERG COMMUNITY HOSPITAL...   
4897                                    HILLSIDE CENTER   

             provider_address provider_city provider_state provider_zip  \
4893  208 WEST TWELFTH STREET        LONDON             KY        40743   
4894   1401 SOUTH 16TH STREET        MURRAY             KY        42071   
4895  201 SOUTH WARREN STREET    MORGANTOWN             KY        42261   
4896  440 HOPKINSVILLE STREET    GREENVILLE             KY        42345   
4897        1500 PRIDE AVENUE  MADISONVILLE             KY        42431   

     provider_phone_number      county submitted_data data_passed_qa  \
4893            6068644155      Laurel              Y              Y   
4894            2707522900    Calloway              Y              Y   
4895            2705263368      Butler              Y              Y   
4896            2703388433  Muhlenberg              N            NaN   
4897            2708211813     Hopkins              N            NaN   

      num_all_beds  num_occ_beds short_nrsg_staff short_aides  \
4893         160.0         146.0              NaN         NaN   
4894         226.0         121.0                Y           N   
4895         122.0         112.0              NaN         NaN   
4896          45.0          37.0              NaN         NaN   
4897          71.0          62.0              NaN         NaN   

      res_wk_confirmed_c19  wk_res_confirmed_c19_cases_per_1000  \
4893                   0.0                                 0.00   
4894                   2.0                                16.53   
4895                   0.0                                 0.00   
4896                   0.0                                 0.00   
4897                   0.0                                 0.00   

      num_staff_new_pos_c19_test  num_res_in_facility  num_res_comp_c19_vax  \
4893                         1.0                146.0                 142.0   
4894                         0.0                118.0                 105.0   
4895                         0.0                  NaN                   NaN   
4896                         NaN                  NaN                   NaN   
4897                         NaN                  NaN                   NaN   

      num_res_offered_declined_cvd_vax  pct_res_comp_c19_vax  num_hcp  \
4893                               3.0                97.260    220.0   
4894                              11.0                88.983    196.0   
4895                               NaN                   NaN      NaN   
4896                               NaN                   NaN      NaN   
4897                               NaN                   NaN      NaN   

      num_hcp_comp_c19_vax  num_hcp_offered_declined_c19_vax  \
4893                 210.0                               0.0   
4894                 155.0                              29.0   
4895                   NaN                               NaN   
4896                   NaN                               NaN   
4897                   NaN                               NaN   

      pct_hcp_comp_c19_vax week_start month_year  
4893                95.455 2022-11-21    2022-11  
4894                79.082 2022-11-21    2022-11  
4895                   NaN 2022-11-21    2022-11  
4896                   NaN 2022-11-21    2022-11  
4897                   NaN 2022-11-21    2022-11

In [175]:
# who failed dq check and how many for how many occurances (weeks)?
nh_ky.loc[nh_ky['data_passed_qa']=='N'].provider_name.value_counts()

KINGS DAUGHTERS MEDICAL CENTER                        73
FLAGET MEMORIAL HOSPITAL NF                           62
BRECKINRIDGE MEMORIAL NURSING FACILITY                53
ST CLAIRE MEDICAL CENTER                              42
NIM HENSON GERIATRIC CENTER                           17
RIVER HAVEN NURSING AND REHABILITATION CENTER         15
BAPTIST HEALTH HARDIN                                  8
FRANKLIN-SIMPSON NURSING AND REHABILITATION CENTER     7
SALYERSVILLE NURSING AND REHABILITATION CENTER         4
SIGNATURE HEALTHCARE OF HART COUNTY REHAB & WELLNE     4
PARKVIEW POST-ACUTE AND REHABILITATION CENTER          3
WEST LIBERTY NURSING AND REHABILITATION                3
FOUNTAIN CIRCLE CARE & REHABILITATION CENTER           3
SIGNATURE HEALTHCARE OF GLASGOW REHAB & WELLNESS C     2
LYNDON WOODS CARE & REHAB, LLC                         2
LANDMARK OF DANVILLE REHABILITATION AND NURSING CE     1
SANSBURY CARE CENTER                                   1
CLIFTON OAKS CARE AND REHAB CEN

In [176]:
nh_ky_pass=nh_ky.loc[nh_ky['data_passed_qa']=='Y']
nh_ky_pass.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 20015 entries, 4893 to 1129538
Data columns (total 28 columns):
 #   Column                               Non-Null Count  Dtype         
---  ------                               --------------  -----         
 0   week_ending                          20015 non-null  datetime64[ns]
 1   federal_provider_number              20015 non-null  object        
 2   provider_name                        20015 non-null  object        
 3   provider_address                     20015 non-null  object        
 4   provider_city                        20015 non-null  object        
 5   provider_state                       20015 non-null  object        
 6   provider_zip                         20015 non-null  object        
 7   provider_phone_number                20015 non-null  object        
 8   county                               20015 non-null  object        
 9   submitted_data                       20015 non-null  object        
 10  data_

In [185]:
# subset to jefferson county
jeff_cty_pass=nh_ky_pass.loc[(nh_ky_pass['month_year']>='2021-07') & (nh_ky_pass['data_passed_qa']=='Y') & (nh_ky_pass['county']=='Jefferson')].sort_values(by=['provider_name','week_ending'])

#sort by facility, week ending date, num_res_in_facility
jeff_cty_pass.sort_values(['federal_provider_number','week_ending','num_res_in_facility'])


week_ending federal_provider_number  \
338156   2021-07-11                  185029   
353407   2021-07-18                  185029   
368658   2021-07-25                  185029   
383905   2021-08-01                  185029   
399151   2021-08-08                  185029   
414395   2021-08-15                  185029   
429639   2021-08-22                  185029   
444884   2021-08-29                  185029   
460129   2021-09-05                  185029   
475373   2021-09-12                  185029   
490618   2021-09-19                  185029   
505862   2021-09-26                  185029   
521104   2021-10-03                  185029   
536344   2021-10-10                  185029   
551582   2021-10-17                  185029   
566821   2021-10-24                  185029   
582059   2021-10-31                  185029   
597297   2021-11-07                  185029   
612532   2021-11-14                  185029   
627760   2021-11-21                  185029   
642986   2021-11-28                  185029   
658213   2021-12-05                  185029   
673436   2021-12-12                  185029   
688657   2021-12-19                  185029   
703877   2021-12-26                  185029   
719096   2022-01-02                  185029   
734305   2022-01-09                  185029   
749514   2022-01-16                  185029   
764721   2022-01-23                  185029   
779929   2022-01-30                  185029   
795137   2022-02-06                  185029   
810341   2022-02-13                  185029   
825544   2022-02-20                  185029   
840745   2022-02-27                  185029   
855941   2022-03-06                  185029   
871133   2022-03-13                  185029   
886325   2022-03-20                  185029   
901517   2022-03-27                  185029   
916710   2022-04-03                  185029   
931902   2022-04-10                  185029   
947093   2022-04-17                  185029   
962282   2022-04-24                  185029   
977470   2022-05-01                  185029   
992655   2022-05-08                  185029   
1007838  2022-05-15                  185029   
1023020  2022-05-22                  185029   
1038201  2022-05-29                  185029   
1053381  2022-06-05                  185029   
1068561  2022-06-12                  185029   
1083739  2022-06-19                  185029   
1098916  2022-06-26                  185029   
1114091  2022-07-03                  185029   
1129266  2022-07-10                  185029   
156215   2022-07-17                  185029   
171360   2022-07-24                  185029   
186504   2022-07-31                  185029   
201648   2022-08-07                  185029   
216790   2022-08-14                  185029   
231930   2022-08-21                  185029   
247069   2022-08-28                  185029   
262205   2022-09-04                  185029   
277342   2022-09-11                  185029   
292478   2022-09-18                  185029   
20031    2022-09-25                  185029   
35165    2022-10-02                  185029   
50296    2022-10-09                  185029   
65426    2022-10-16                  185029   
80557    2022-10-23                  185029   
95688    2022-10-30                  185029   
110819   2022-11-06                  185029   
125949   2022-11-13                  185029   
141079   2022-11-20                  185029   
4900     2022-11-27                  185029   
338158   2021-07-11                  185039   
353409   2021-07-18                  185039   
368660   2021-07-25                  185039   
383907   2021-08-01                  185039   
399153   2021-08-08                  185039   
414397   2021-08-15                  185039   
429641   2021-08-22                  185039   
444886   2021-08-29                  185039   
460131   2021-09-05                  185039   
475375   2021-09-12                  185039   
490620   2021-09-19                  185039   
505864   2021

In [196]:
jeff_cty_pass.loc[jeff_cty_pass['num_res_in_facility'].isnull()].sort_values('week_ending')

week_ending federal_provider_number  \
429895   2021-08-22                  185468   
505925   2021-09-26                  185175   
703896   2021-12-26                  185095   
734457   2022-01-09                  185305   
992909   2022-05-08                  185468   
1008092  2022-05-15                  185468   
1007858  2022-05-15                  185096   
1023040  2022-05-22                  185096   
1023274  2022-05-22                  185468   
1038455  2022-05-29                  185468   
1038221  2022-05-29                  185096   
1053635  2022-06-05                  185468   
1053401  2022-06-05                  185096   
1068581  2022-06-12                  185096   
1068815  2022-06-12                  185468   
1083759  2022-06-19                  185096   
1083993  2022-06-19                  185468   
1098936  2022-06-26                  185096   
1099170  2022-06-26                  185468   
1114111  2022-07-03                  185096   
1114345  2022-07-03                  185468   
1129332  2022-07-10                  185178   
1129474  2022-07-10                  185388   
1129514  2022-07-10                  185462   
1129452  2022-07-10                  185348   
1129421  2022-07-10                  185310   
1129536  2022-07-10                  185485   
1129418  2022-07-10                  185305   
1129300  2022-07-10                  185137   
1129518  2022-07-10                  185466   
1129365  2022-07-10                  185237   
1129391  2022-07-10                  185268   
1129296  2022-07-10                  185132   
1129266  2022-07-10                  185029   
1129513  2022-07-10                  185461   
1129529  2022-07-10                  185478   
156468   2022-07-17                  185468   
95722    2022-10-30                  185137   
141132   2022-11-20                  185165   
5025     2022-11-27                  185268   
5086     2022-11-27                  185348   
5162     2022-11-27                  185478   
5169     2022-11-27                  185485   
5052     2022-11-27                  185305   
4930     2022-11-27                  185132   
4999     2022-11-27                  185237   
4934     2022-11-27                  185137   
4900     2022-11-27                  185029   
4970     2022-11-27                  185192   
5088     2022-11-27                  185350   
4920     2022-11-27                  185096   
5161     2022-11-27                  185477   
5049     2022-11-27                  185300   
5056     2022-11-27                  185311   
5087     2022-11-27                  185349   
4957     2022-11-27                  185169   
5147     2022-11-27                  185462   
5136     2022-11-27                  185442   
4935     2022-11-27                  185138   
5108     2022-11-27                  185388   
5146     2022-11-27                  185461   
4953     2022-11-27                  185165   
5075     2022-11-27                  185335   
5151     2022-11-27                  185466   

                                             provider_name  \
429895   LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
505925                                  TREYTON OAK TOWERS   
703896                       HILLCREEK REHAB AND CARE, LLC   
734457                 THE WILLOWS AT SPRINGHURST OPCO LLC   
992909   LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
1008092  LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
1007858  LANDMARK OF IROQUOIS PARK REHAB AND NURSING CE...   
1023040  LANDMARK OF IROQUOIS PARK REHAB AND NURSING CE...   
1023274  LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
1038455  LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
1038221  LANDMARK OF IROQUOIS PARK REHAB AND NURSING CE...   
1053635  LANDMARK OF RIVER CITY REHABILITATION AND NURSING   
1053401  LANDMARK OF IROQUOIS PARK REHAB AND NURSING CE...   
1068581  LANDMARK OF IROQUOIS PARK REHAB AND NURSING CE...   
1068815  LANDMARK OF R

In [190]:
jeff_cty_pass.federal_provider_number.value_counts()

185237    73
185388    73
185029    73
185259    73
185456    73
185169    73
185349    73
185311    73
185477    73
185350    73
185335    73
185348    73
185310    73
185485    73
185305    73
185175    73
185137    73
185138    73
185462    73
185268    73
185361    73
185288    73
185478    73
185132    73
185461    73
185039    73
185095    73
185154    73
185178    73
185466    73
185260    73
185300    72
185096    72
185192    72
185442    72
185455    72
185176    72
185333    71
185290    71
185136    71
185165    71
185468    63
185122    60
185301    10
Name: federal_provider_number, dtype: int64

In [191]:
# Why does 185301 only have 10 occurrences? 

jeff_cty_pass.loc[jeff_cty_pass['federal_provider_number'] == '185301']

# Regis Woods. Shut down sept 2021 for health and safety violations: 
# https://www.courier-journal.com/story/news/local/2021/09/15/louisville-nursing-home-regis-woods-losing-medicaid-funding-residents-relocated/8349023002/


week_ending federal_provider_number provider_name provider_address  \
338307  2021-07-11                  185301   REGIS WOODS   4604 LOWE ROAD   
353558  2021-07-18                  185301   REGIS WOODS   4604 LOWE ROAD   
368809  2021-07-25                  185301   REGIS WOODS   4604 LOWE ROAD   
384056  2021-08-01                  185301   REGIS WOODS   4604 LOWE ROAD   
399302  2021-08-08                  185301   REGIS WOODS   4604 LOWE ROAD   
414546  2021-08-15                  185301   REGIS WOODS   4604 LOWE ROAD   
429790  2021-08-22                  185301   REGIS WOODS   4604 LOWE ROAD   
445035  2021-08-29                  185301   REGIS WOODS   4604 LOWE ROAD   
460279  2021-09-05                  185301   REGIS WOODS   4604 LOWE ROAD   
475523  2021-09-12                  185301   REGIS WOODS   4604 LOWE ROAD   

       provider_city provider_state provider_zip provider_phone_number  \
338307    LOUISVILLE             KY        40220            5024511401   
353558    LOUISVILLE             KY        40220            5024511401   
368809    LOUISVILLE             KY        40220            5024511401   
384056    LOUISVILLE             KY        40220            5024511401   
399302    LOUISVILLE             KY        40220            5024511401   
414546    LOUISVILLE             KY        40220            5024511401   
429790    LOUISVILLE             KY        40220            5024511401   
445035    LOUISVILLE             KY        40220            5024511401   
460279    LOUISVILLE             KY        40220            5024511401   
475523    LOUISVILLE             KY        40220            5024511401   

           county submitted_data data_passed_qa  num_all_beds  num_occ_beds  \
338307  Jefferson              Y              Y         186.0         123.0   
353558  Jefferson              Y              Y         186.0         123.0   
368809  Jefferson              Y              Y         186.0         120.0   
384056  Jefferson              Y              Y         186.0         117.0   
399302  Jefferson              Y              Y         186.0         116.0   
414546  Jefferson              Y              Y         186.0         115.0   
429790  Jefferson              Y              Y         186.0         115.0   
445035  Jefferson              Y              Y         186.0         113.0   
460279  Jefferson              Y              Y         186.0         113.0   
475523  Jefferson              Y              Y         186.0         112.0   

       short_nrsg_staff short_aides  res_wk_confirmed_c19  \
338307                N           N                   0.0   
353558                N           N                   0.0   
368809                N           N                   0.0   
384056                N           N                   0.0   
399302                N           N                   0.0   
414546                N           N                   0.0   
429790                N           N                   0.0   
445035                N           N                   0.0   
460279                N           N                   0.0   
475523                N           N                   0.0   

        wk_res_confirmed_c19_cases_per_1000  num_staff_new_pos_c19_test  \
338307                                  0.0                         0.0   
353558                                  0.0                         0.0   
368809                                  0.0                         0.0   
384056                                  0.0                         0.0   
399302                                  0.0                         0.0   
414546                                  0.0                         0.0   
429790                                  0.0                         0.0   
445035                                  0.0                         0.0   
460279                                  0.0                         0.0   
475523                                  0.0         

In [192]:
# Regis Woods. Shut down sept 2021 for health and safety violations: 
# https://www.courier-journal.com/story/news/local/2021/09/15/louisville-nursing-home-regis-woods-losing-medicaid-funding-residents-relocated/8349023002/


### What did Jefferson county nh staff vax rates and res vax rates look like over the past year? (Median and Mean)


In [193]:
jeff_cty_pass_avg_med=jeff_cty_pass.groupby(['month_year','county'],dropna=False).agg(
sum_hcp_comp_c19_vax=('num_hcp_comp_c19_vax','sum'),
sum_hcp=('num_hcp','sum'),
sum_res_comp_c19_vax=('num_res_comp_c19_vax','sum'),
sum_res_in_facility=('num_res_in_facility','sum'),
pct_hcp_comp_c19_vax_median=('pct_hcp_comp_c19_vax','median'),
pct_res_comp_c19_vax_median=('pct_res_comp_c19_vax','median')).reset_index()


In [194]:
jeff_cty_pass_avg_med['pct_hcp_comp_c19_vax_avg'] = jeff_cty_pass_avg_med['sum_hcp_comp_c19_vax']/jeff_cty_pass_avg_med['sum_hcp']*100
jeff_cty_pass_avg_med['pct_res_comp_c19_vax_avg'] = jeff_cty_pass_avg_med['sum_res_comp_c19_vax']/jeff_cty_pass_avg_med['sum_res_in_facility']*100


In [195]:
jeff_cty_pass_avg_med

month_year     county  sum_hcp_comp_c19_vax  sum_hcp  sum_res_comp_c19_vax  \
0     2021-07  Jefferson               12319.0  21611.0               11415.0   
1     2021-08  Jefferson               15623.0  26043.0               14551.0   
2     2021-09  Jefferson               13616.0  21030.0               11617.0   
3     2021-10  Jefferson               15019.0  21229.0               12047.0   
4     2021-11  Jefferson               20825.0  27018.0               15250.0   
5     2021-12  Jefferson               17571.0  21037.0               12221.0   
6     2022-01  Jefferson               21677.0  25522.0               14634.0   
7     2022-02  Jefferson               18539.0  20961.0               11938.0   
8     2022-03  Jefferson               19810.0  21792.0               12326.0   
9     2022-04  Jefferson               20787.0  22624.0               12735.0   
10    2022-05  Jefferson               26386.0  28923.0               15379.0   
11    2022-06  Jefferson               20696.0  22630.0               11851.0   
12    2022-07  Jefferson               19163.0  21244.0               11353.0   
13    2022-08  Jefferson               27797.0  30485.0               16098.0   
14    2022-09  Jefferson               21812.0  23924.0               13065.0   
15    2022-10  Jefferson               26566.0  28967.0               16017.0   
16    2022-11  Jefferson               12184.0  13239.0                7648.0   

    sum_res_in_facility  pct_hcp_comp_c19_vax_median  \
0               14578.0                      59.5840   
1               18201.0                      63.4920   
2               14279.0                      69.7990   
3               14582.0                      77.2930   
4               18120.0                      81.8665   
5               14208.0                      86.3775   
6               17010.0                      88.6105   
7               13783.0                      92.1725   
8               14173.0                      93.0560   
9               14614.0                      94.3365   
10              17587.0                      94.4695   
11              13499.0                      93.2895   
12              13032.0                      92.9650   
13              18781.0                      92.7080   
14              15099.0                      92.7930   
15              18449.0                      92.9130   
16               8797.0                      92.5020   

    pct_res_comp_c19_vax_median  pct_hcp_comp_c19_vax_avg  \
0                       80.0000                 57.003378   
1                       81.3950                 59.989249   
2                       84.3140                 64.745602   
3                       86.5155                 70.747562   
4                       86.9570                 77.078244   
5                       87.5000                 83.524267   
6                       88.2980                 84.934566   
7                       88.6945                 88.445208   
8                       89.0410                 90.904919   
9                       89.1890                 91.880304   
10                      88.5385                 91.228434   
11                      89.7510                 91.453822   
12                      91.5790                 90.204293   
13                      90.6980                 91.182549   
14                      89.9440                 91.172045   
15                      88.7320                 91.711258   
16                      89.5965                 92.031120   

    pct_res_comp_c19_vax_avg  
0                  78.302922  
1                  79.946157  
2                  81.357238  
3                  82.615553  
4                  84.161148  
5                  86.014921  
6                  86.031746  
7                  86.613945  
8                  86.968179  
9                  87.142466  
10                 87.445272  
11                 87.791688  
12                 87.116329  
13

### Plot: distribution of staff vax and res vax pcts for Jefferson county by month-yr

In [207]:
jeff_cty_pass['month_year'] = pd.to_datetime(jeff_cty_pass['month_year'], format='%Y-%m')


fig = px.box(jeff_cty_pass, x='month_year', y='pct_hcp_comp_c19_vax', points='all')

fig.update_layout(
    autosize=False,
    width=1200,
    height=600
)

fig.show()

ERROR! Session/line number was not unique in database. History logging moved to new session 403


### WIP see below

In [ ]:
## box plot
jeff_cty_pass_fig = px.box(
    jeff_cty_pass, 
    x = pd.to_datetime('week_start'),
    y = 'pct_hcp_comp_c19_vax',
    title = 'Pct healthcare staff who completed covid-19 vaccination',
    points = 'all', # will display dots next to the boxes 
    labels = {
        'x': pd.to_datetime('week_start'),
        'y': 'pct_hcp_comp_c19_vax'
    }
)

jeff_cty_pass_fig.update_layout(
    plot_bgcolor = 'white',
    xaxis = dict(
        showline = True,
        linecolor = 'black'
    ),
    
    yaxis = dict(
        showline = True,
        showgrid = False,
        linecolor = 'black'
    )
    
)

jeff_cty_pass_fig.show()

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



TypeError: Unrecognized value type: <class 'str'>

During handling of the above exception, another exception occurred:

dateutil.parser._parser.ParserError: Unknown string format: week_start

During handling of the above exception, another exception occurred:

AttributeError: 'ParserError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

AssertionError
TypeError: Unrecognized value type: <class 'str'>

During handling of the above exception, another exception occurred:

dateutil.parser._parser.ParserError: Unknown string format: week_start

During handling of the above exception, another exception occurred:

AttributeError: 'ParserError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

TypeError: object of type 'NoneType' has no len()

During handling of the above exception, another exception occurred:

AttributeError: 'TypeError' object has no attribute '

### Plot time series line for Jefferson county by month

## nelson county subset

In [ ]:
# subset to nelson county, ky
nh_ky_cty_nelson = nh_ky.loc[nh_ky.county=='Nelson'].reset_index(drop=True)
nh_ky_cty_nelson.sort_values(by=['provider_name','week_ending'])

In [ ]:
nh_ky_cty_nelson.info()

In [ ]:
nh_ky_cty_nelson.provider_name.value_counts()

In [ ]:
nh_ky_cty_nelson.loc[(nh_ky_cty_nelson['month_year']>='2021-10') & (nh_ky_cty_nelson['data_passed_qa']=='Y')].sort_values(by=['provider_name','week_ending'])

In [ ]:
nh_ky_cty_nelson.loc[(nh_ky_cty_nelson['month_year']>='2021-10') & (nh_ky_cty_nelson['data_passed_qa']=='Y')].quantile([0, .1, .25, .33, .5, .67, .75, .9, 1])

In [ ]:
nh_ky_cty_nelson.loc[(nh_ky_cty_nelson['month_year']>='2022-04') & (nh_ky_cty_nelson['data_passed_qa']=='Y')].pct_hcp_comp_c19_vax.mean()

In [ ]:
nh_ky_cty_nelson.loc[(nh_ky_cty_nelson['month_year']>='2022-04') & (nh_ky_cty_nelson['data_passed_qa']=='Y')].pct_hcp_comp_c19_vax.median()

## Shapefile data

In [ ]:
# Read in shp file as dataframe
# Nursing home shapefile data source: HIFLD data retrieved from: 
# https://hifld-geoplatform.opendata.arcgis.com/datasets/geoplatform::nursing-homes/about
# Latest update for files: Jun 29, 22

nh_shp_df = gpd.read_file('data/Nursing_Homes_shape/NursingHomes.shp')
nh_shp_df.head()

In [ ]:
nh_shp_df.info()

In [ ]:
nh_shp_df.loc[nh_shp_df['NAME']=='CHEROKEE PARK REHABILITATION']